In [1]:
# This one gets all table data text
import re
import numpy as np
import pandas as pd
import requests
from bs4 import BeautifulSoup
import csv
from urllib.parse import urlparse

In [2]:
DATA_FOLDER = "/Users/noopy/Yonsei_Exchange_Text_Wrangling/data/"
UNIV_DATA_FILE = "univ_db_full.csv"

In [3]:
#HTML tag removal function
def remove_tag(content):
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', content)
    return cleantext

#make country code list
def make_con_code_list():
    doc = """
    <option value="AF">AFGHANISTAN</option><option value="AR">ARGENTINA</option><option value="AU">AUSTRALIA</option><option value="AT">AUSTRIA</option><option value="BD">BANGLADESH</option><option value="BE">BELGIUM</option><option value="BR">BRAZIL</option><option value="BN">BRUNEI</option><option value="BG">BULGARIA</option><option value="KH">CAMBODIA</option><option value="CA">CANADA</option><option value="CL">CHILE</option><option value="CN">CHINA</option><option value="CR">COSTA RICA</option><option value="CZ">CZECH REPUBLIC</option><option value="DK">DENMARK</option><option value="EE">ESTONIA</option><option value="FI">FINLAND</option><option value="FR">FRANCE</option><option value="DE">GERMANY</option><option value="GH">GHANA</option><option value="HK">HONG KONG</option><option value="HU">HUNGARY</option><option value="IS">ICELAND</option><option value="IN">INDIA</option><option value="ID">INDONESIA</option><option value="IR">IRAN</option><option value="IE">IRELAND</option><option value="IL">ISRAEL</option><option value="IT">ITALY</option><option value="JP">JAPAN</option><option value="JO">JORDAN</option><option value="KZ">KAZAKHSTAN</option><option value="LV">LATVIA</option><option value="LT">LITHUANIA</option><option value="MY">MALAYSIA</option><option value="MT">MALTA</option><option value="MX">MEXICO</option><option value="MN">MONGOLIA</option><option value="NP">NEPAL</option><option value="NL">NETHERLANDS</option><option value="NZ">NEW ZEALAND</option><option value="NI">NICARAGUA</option><option value="NO">NORWAY</option><option value="PH">PHILIPPINES</option><option value="PL">POLAND</option><option value="PT">PORTUGAL</option><option value="PR">PUERTO RICO</option><option value="RU">RUSSIAN FEDERATION</option><option value="SG">SINGAPORE</option><option value="ZA">SOUTH AFRICA</option><option value="ES">SPAIN</option><option value="SE">SWEDEN</option><option value="CH">SWITZERLAND</option><option value="TW">TAIWAN</option><option value="TH">THAILAND</option><option value="TR">TURKEY</option><option value="GB">UNITED KINGDOM</option><option value="US">UNITED STATES</option><option value="UY">URUGUAY</option><option value="VN">VIETNAM</option><option value="ZW">ZIMBABWE</option>
    """

    #Separating doc HTML
    soup_concod=BeautifulSoup(doc,'lxml')
    list_concod=soup_concod.findAll('option')
    #print(list_concod)

    #Parsing Country Name String List
    soup_con=BeautifulSoup(doc,'lxml')
    list_con= [str(x.text) for x in soup_con.find_all('option')]
    #print(list_con)

    list_con_abv = []
    con_numb=0
    while con_numb < len(list_con) :
        #extracting individual country codes
        item_concod=list_concod[con_numb]
        str_item_concod=str(item_concod)
        code= str_item_concod[15:17]
        list_con_abv.append(code)
        con_numb+=1
    print(list_con_abv)
    return list_con_abv

#make universities' dataset for each countries
def make_univ_db(folder_path):
    dummy_data1 = {}
    df = pd.DataFrame(dummy_data1)

    # country_list = make_con_code_list()
    country_list = ['AF', 'AR', 'AU', 'AT', 'BD', 'BE', 'BR', 'BN', 'BG', 'KH', 'CA', 'CL', 'CN', 'CR', 'CZ', 'DK', 'EE', 'FI', 'FR', 'DE', 'GH', 'HK', 'HU', 'IS', 'IN', 'ID', 'IR', 'IE', 'IL', 'IT', 'JP', 'JO', 'KZ', 'LV', 'LT', 'MY', 'MT', 'MX', 'MN', 'NP', 'NL', 'NZ', 'NI', 'NO', 'PH', 'PL', 'PT', 'PR', 'RU', 'SG', 'ZA', 'ES', 'SE', 'CH', 'TW', 'TH', 'TR', 'GB', 'US', 'UY', 'VN', 'ZW']
    # country_list = ['AU','DK','FI']
    for country in country_list:
        url = "https://oia.yonsei.ac.kr/partner/expReport.asp?yn=Y&country_code="+country+"&univ="
        res = requests.get(url)
        soup = BeautifulSoup(res.content,'lxml')
        table = soup.find_all('table')[0]
        df_crawl = pd.read_html(str(table),encoding='utf-8', header=0)[0]
        # print(df_crawl)
        df_crawl['href'] = [np.where(tag.has_attr('href'),tag.get('href'),"no link") for tag in table.find_all('a')]
#         print(df_crawl)
        df = pd.concat([df, df_crawl],sort=False)
    df_without_index = df.reset_index()
    print(df_without_index)
    df_without_index.to_csv(folder_path+"univ_db_full.csv",index=False,encoding="utf-8")

In [4]:
make_univ_db(DATA_FOLDER)

     index  No                                            대학명           국가  \
0        0   1                               Kabul University  AFGHANISTAN   
1        0   1                        Universidad Blas Pascal    ARGENTINA   
2        1   2                Universidad Catolica de Cordoba    ARGENTINA   
3        2   3                         Universidad de Palermo    ARGENTINA   
4        3   4                       Universidad del Salvador    ARGENTINA   
..     ...  ..                                            ...          ...   
740      2   3         National Economics University of Hanoi      VIETNAM   
741      3   4             Vietnam National University, Hanoi      VIETNAM   
742      4   5  Vietnam National University, Ho Chi Minh City      VIETNAM   
743      5   6                                 Vin University      VIETNAM   
744      0   1                         University of Zimbabwe     ZIMBABWE   

     파견구분  협정형태                                          href  

In [5]:
df_univ = pd.read_csv(DATA_FOLDER+UNIV_DATA_FILE)
df_univ.head()

index  No                              대학명           국가  파견구분  협정형태  \
0      0   1                 Kabul University  AFGHANISTAN  교환학생  교환대학   
1      0   1          Universidad Blas Pascal    ARGENTINA  교환학생  ISEP   
2      1   2  Universidad Catolica de Cordoba    ARGENTINA  교환학생  ISEP   
3      2   3           Universidad de Palermo    ARGENTINA  교환학생  ISEP   
4      3   4         Universidad del Salvador    ARGENTINA  교환학생  ISEP   

                                           href  
0  /partner/expReport.asp?ucode=AF000001&bgbn=A  
1  /partner/expReport.asp?ucode=AR000001&bgbn=A  
2  /partner/expReport.asp?ucode=AR000002&bgbn=A  
3  /partner/expReport.asp?ucode=AR000003&bgbn=A  
4  /partner/expReport.asp?ucode=AR000004&bgbn=A

In [6]:
# check the whether the exchange university was ever visited in the past
def count_reviews(folder_path, file_name):
    df_univ = pd.read_csv(folder_path+file_name)
    review_existence_list = []
    for univ_query in df_univ["href"]:
        url = "https://oia.yonsei.ac.kr" + univ_query
        res = requests.get(url)
        soup = BeautifulSoup(res.content,'lxml')
        table = soup.find_all('table')[0]
        df_crawl = pd.read_html(str(table),encoding='utf-8', header=0)[0]
        if df_crawl.empty:
            print(f"nobody ever went to {univ_query}")
            review_existence_list.append("None")
        if not df_crawl.empty:
            review_existence_list.append("Exists")
    return review_existence_list

In [7]:
visitation_TF = count_reviews(DATA_FOLDER, UNIV_DATA_FILE)

nobody ever went to /partner/expReport.asp?ucode=AF000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AR000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AR000002&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AR000003&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AR000005&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AU000021&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AU000006&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AU000009&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AU000011&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AU000022&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AU000017&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AT000004&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=AT000005&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=BD000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=BE000004&bgbn=A
nobody ever went to /part

nobody ever went to /partner/expReport.asp?ucode=MN000003&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=NP000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=NP000002&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=NL000017&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=NI000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=NO000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=NO000004&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=PT000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=PR000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=ZA000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=ES000004&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=ES000005&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=ES000007&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=ES000009&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=SE000009&bgbn=A
nobody ever went to /part

nobody ever went to /partner/expReport.asp?ucode=US000251&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000253&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000256&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000257&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000262&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000266&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000269&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000270&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000144&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000275&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000276&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=US000277&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=UY000001&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=VN000002&bgbn=A
nobody ever went to /partner/expReport.asp?ucode=VN000004&bgbn=A
nobody ever went to /part

In [8]:
df_univ["visitation"]= visitation_TF
df_univ.head()

index  No                              대학명           국가  파견구분  협정형태  \
0      0   1                 Kabul University  AFGHANISTAN  교환학생  교환대학   
1      0   1          Universidad Blas Pascal    ARGENTINA  교환학생  ISEP   
2      1   2  Universidad Catolica de Cordoba    ARGENTINA  교환학생  ISEP   
3      2   3           Universidad de Palermo    ARGENTINA  교환학생  ISEP   
4      3   4         Universidad del Salvador    ARGENTINA  교환학생  ISEP   

                                           href visitation  
0  /partner/expReport.asp?ucode=AF000001&bgbn=A       None  
1  /partner/expReport.asp?ucode=AR000001&bgbn=A       None  
2  /partner/expReport.asp?ucode=AR000002&bgbn=A       None  
3  /partner/expReport.asp?ucode=AR000003&bgbn=A       None  
4  /partner/expReport.asp?ucode=AR000004&bgbn=A     Exists

In [9]:
df_univ.tail()

index  No                                            대학명        국가  파견구분  \
740      2   3         National Economics University of Hanoi   VIETNAM  교환학생   
741      3   4             Vietnam National University, Hanoi   VIETNAM  교환학생   
742      4   5  Vietnam National University, Ho Chi Minh City   VIETNAM   NaN   
743      5   6                                 Vin University   VIETNAM   NaN   
744      0   1                         University of Zimbabwe  ZIMBABWE  교환학생   

     협정형태                                          href visitation  
740   NaN  /partner/expReport.asp?ucode=VN000001&bgbn=A       None  
741  교환대학  /partner/expReport.asp?ucode=VN000003&bgbn=A       None  
742  교환대학  /partner/expReport.asp?ucode=VN000005&bgbn=A       None  
743  교환대학  /partner/expReport.asp?ucode=VN000006&bgbn=A       None  
744  교환대학  /partner/expReport.asp?ucode=ZW000001&bgbn=A       None

In [10]:
df_univ_without_index = df_univ.reset_index()
df_univ_without_index.to_csv(DATA_FOLDER+UNIV_DATA_FILE,index=False,encoding="utf-8")

In [11]:
def crawl_review(href):
    empty_lst = []
    review_url = "https://oia.yonsei.ac.kr" + href
    res = requests.get(review_url)
    soup = BeautifulSoup(res.content,'lxml')
    body_cursor_list = soup.find_all("div", {"class": "exp_txt"})

    text_list = []
    for i in body_cursor_list:
        review_paragraph = i.text.strip()
        text_list.append(review_paragraph)

    text_list = text_list[1:]
    return text_list

In [12]:
crawl_review("/partner/expReport.asp?id=15129&page=1&bgbn=R")

['코펜하겐 대학교는 총 네 개의 캠퍼스로 구성되어 있습니다. 각각의 캠퍼스가 모두 분산되어 있기 때문에 본인이 주로 수업을 듣게 될 학교 근처로 기숙사를 신청하는 걸 추천합니다. 저는 인문대학과 사회과학대학 두 캠퍼스에서 수업을 모두 들어서, 이곳저곳 옮겨다녀야 했습니다. 인문대학은 공사한지 얼마 되지 않아(제가 다니는 도중에도 여전히 공사중이었습니다.) 송도캠퍼스처럼 새 건물의 느낌을 풍깁니다. 사회과학대학은 이전에 병원이었던 건물을 개조하여 캠퍼스로 사용하고 있는데, 오래된 건물만이 줄 수 있는 특유의 고풍스러움을 풍깁니다. 인문대학에 비해 그렇게 크게 느껴지진 않습니다. 그러나 코펜하겐의 중심부에 위치하고 있어서 학교 바로 근처에 온갖 시내와 관광명소를 돌아다닐 수 있다는 장점이 있습니다.저는 8월 3일부터 1월 중순까지 있었는데, 유럽의 가을 겨울이 지독하게 흐리고 우중충하다는 소리를 하도 들어서 미리 마음의 준비를 해서 그런지 그렇게 나쁘게 느껴지진 않았습니다. 9월까지는 비교적 쨍쨍한 날들이 지속된 것 같아요. 10월부턴 한 달에 4일..? 하루 종일 맑은 것도 아니고, 해가 잠깐 뜬 날까지 합해서 4일 정도 있었던 것 같아요... 정말 매일매일이 우중충하고 흐립니다. 여기에서의 하늘색은 파란 계열이 아니라 회색/흰색 계열이에요ㅎㅎ 그래서 해가 잠깐이라도 뜨면 무조건! 뛰쳐나갔던 것 같아요 수업도 째고... 기온은 그렇게 낮진 않은데(영하로 내려갔던 적이 거의 없었던 것 같아요) 섬이다 보니까 바닷바람이 엄청 세요. 송도를 상상하시면 될 것 같습니다... 기온 자체는 낮지 않은데 해도 없고 바람도 엄청 불어서 한국만큼 추웠어요... 전기요 필수입니다..',
 '인문대학 주변엔 딱히 뭐가 없어요. 인문대는 Amager 섬에 따로 위치해 있어서, 코펜하겐이라고 치지 않는 것 같더라구요. 이 섬에서 코펜하겐 중앙 본섬으로 넘어가면 사회과학대학이 있습니다. 사회과학대는 도심 중심에 위치해 있어서 주위에 뭐가 많아요. 우리나라로 치면 명동이라 할 수 있는 

In [26]:
# crawl students' reviews for university
def collect_avail_reviews(download_folder, univ_query):
    page = 1
    dummy_data1 = {}
    df = pd.DataFrame(dummy_data1)
    while page:
        url = f"https://oia.yonsei.ac.kr/partner/expReport.asp?page={page}&cur_pack=0&ucode={univ_query}&bgbn=A"
        res = requests.get(url)
        soup = BeautifulSoup(res.content,'lxml')
        table = soup.find_all('table')[0]
        df_crawl = pd.read_html(str(table),encoding='utf-8', header=0)[0]
        df_crawl['href'] = [np.where(tag.has_attr('href'),tag.get('href'),"no link") for tag in table.find_all('a')]
        if not df_crawl.empty:
            page += 1
            df = pd.concat([df, df_crawl],sort=False)
        else:
            print(df)
            break
    df.to_csv(download_folder+univ_query+'_review_abstract.csv',index=False,encoding="utf-8")

def make_reviews_textdata_for_each_univ(download_folder, univ_code):
    initial_df = pd.read_csv(download_folder+univ_code+"_review_abstract.csv")
    stacked_list = []
    for item in initial_df['href']:
        print(item)
        text_list = crawl_review(item)
        stacked_list.append(text_list)
    univ_text_df= pd.DataFrame(np.row_stack(stacked_list),
                               columns=["gen_info", "env_info", "food_info", "study_info", "office_info", "facil_info", "mhct_info","help_info","etc_info"])
    print(univ_text_df)
    univ_text_df.to_csv(download_folder+univ_code+'_reviews_specific.csv',index=False,encoding="utf-8")

def give_cde_from_url(href):
    query =urlparse(href)
    query_list = query.query.split('=')
    query_list2 = query_list[1].split('&')
    univ_code = query_list2[0]
    print(univ_code)
    return univ_code

def mke_csv_files(folder_path, univ_dataset, download_folder):
    df_univ = pd.read_csv(folder_path + univ_dataset)
    df_with_reviews = df_univ.loc[df_univ["visitation"]=="Exists"]    
    # print(df_with_reviews)
    for href in df_with_reviews["href"]:
        print(href)
        univ_code = give_cde_from_url(href)
        collect_avail_reviews(download_folder, univ_code)
        make_reviews_textdata_for_each_univ(download_folder, univ_code)

In [27]:
TEXT_DATA_FOLDER="/Users/noopy/Yonsei_Exchange_Text_Wrangling/data/univ_text_data/"

In [28]:
mke_csv_files(DATA_FOLDER, UNIV_DATA_FILE, TEXT_DATA_FOLDER)

/partner/expReport.asp?ucode=AR000004&bgbn=A
AR000004
   No                    제목    학과  과정      년도  \
0   1  아르헨티나 교환학생(어학연수프로그램)  건축학과  학부  2013-1   

                                           href  
0  /partner/expReport.asp?id=6947&page=1&bgbn=R  
/partner/expReport.asp?id=6947&page=1&bgbn=R
                                            gen_info  \
0  아르헨티나의 대다수 대학교는 한국처럼 캠퍼스가 있는 것이 아니라 도시 내에 몇개의 ...   

                                            env_info  \
0  대학교가 도시 여러곳에 분포하고 있으므로 각기 다르다. 하지만 남녀를 불문하고 부에...   

                                           food_info  \
0  기숙사는 학교에서 제공하지 않고 두가지 옵션이 주어진다. 홈스테이 혹은 게스트 하우...   

                                          study_info  \
0  아르헨티나에서의 대학 수업은 주로 오전 혹은 저녁에 있다. 대부분의 학생들이 일을하...   

                                         office_info  \
0  EL SALVADOR대학교는 국제 교육부가 잘 되있는 학교이다. 아르헨티나 대학교들...   

                                          facil_info  \
0  부대시설로는 헬스장이 있다고 알고 있으나 시내와 먼 곳에 있었다. 동아리는 몇가지 ...   

                        

   No                           제목       학과  과정         년도  \
0  19              그리운 Bond에서의 한학기   사회복지학과  학부       2014   
1  18       하루하루가 힐링되는 Bond에서의 한학기   식품영양학과  학부       2014   
2  17                호주, 그리고 골드코스트    기계공학과  학부       2011   
3  16           골드코스트에서의 꿈같은 여름 ;)   신문방송학과  학부       2011   
4  15                  bond에서의 나의삶   정치외교학과  학부       2010   
5  14                골드 코스트에서의 3개월    정치외교학  학부       2009   
6  13            지상낙원 골드코스트에서의 한학기     경제학과  학부       2009   
7  12              Bond University     경제학과  학부       2008   
8  11         소중했던 Bond에서의 한 학기 :)   국어국문학과  학부       2008   
9  10             교환학생, 그리고 그것을 넘어  정보산업공학과  학부       2008   
0   9         Bond uni 에서의 잊지못할 추억    도시공학과  학부       2008   
1   8        3막 2장, 본드와의 특별한 인연 ^^   중어중문학과  학부       2007   
2   7     골드코스트에서 보낸 평생 잊지 못할 한 학기   신문방송학과  학부       2006   
3   6            Bond & Gold Coast     경영학과  학부       2006   
4   5              Bond University   불어불문학과  학부       2005   
5   4  M

   No                            제목       학과  과정    년도  \
0   7                    교환학생 경험보고서  글로벌행정학과  학부  2015   
1   6   행복했던 Curtin Universty의 한 학기     경영학과  학부  2015   
2   5             Curtin University   식품영양학과  학부  2015   
3   4                Curtin에서의 한 학기   영어영문학과  학부  2014   
4   3               살기 좋은 도시, perth    경영학전공  학부  2003   
5   2            Curtin Univ. - 원호연   생명공학전공  학부  2001   
6   1  Curtin U of Technology - 유혜승  기계전자공학부  학부  2001   

                                            href  
0  /partner/expReport.asp?id=12693&page=1&bgbn=R  
1  /partner/expReport.asp?id=12162&page=1&bgbn=R  
2  /partner/expReport.asp?id=12156&page=1&bgbn=R  
3  /partner/expReport.asp?id=11963&page=1&bgbn=R  
4   /partner/expReport.asp?id=1022&page=1&bgbn=R  
5    /partner/expReport.asp?id=424&page=1&bgbn=R  
6    /partner/expReport.asp?id=358&page=1&bgbn=R  
/partner/expReport.asp?id=12693&page=1&bgbn=R
/partner/expReport.asp?id=12162&page=1&bgbn=R
/partner/expReport.asp?id=12156&pag

   No                               제목       학과  과정         년도  \
0  24                   행복했던 멜버른에서의 3주     경영학과  학부       2020   
1  23            Deakin 에서의 잊을 수 없는 추억    건축공학과  학부       2019   
2  22             Deakin Burwood에서의 3주      의예과  학부       2020   
3  21                   3주간 여유로웠던 계절학기      의예과  학부       2019   
4  20                 Deakin 대학교에서의 3주   영어영문학과  학부       2020   
5  19          대학생활 최고의 학기를 보낸 교환학생 기간    기계공학과  학부       2019   
6  18               geelong에서의 평화로운 한달     사회학과  학부       2019   
7  17       한 여름 밤의 꿈 같았던 Deakin에서의 3주     경영학과  학부       2019   
8  16               내 인생 최고의 경험을 호주에서,      EIC  학부       2019   
9  15                  질롱에서의 평화로웠던 한달간   실내건축학과  학부       2019   
0  14                 일상이 무료할 때는 디킨으로!  화공생명공학부  학부       2019   
1  13                  디킨, 잊을 수 없는 시간들     경영학과  학부       2019   
2  12         Deakin University에서의 한학기   임상병리학과  학부       2018   
3  11                               1년     간호학과  학부       2017   
4  10     

   No                          제목         학과  과정         년도  \
0  22                  분두라에서 살아남기     불어불문학과  학부       2015   
1  21         정말 기억에 남을 멜버른에서의 추억     영어영문학과  학부       2015   
2  20            한 학기 동안의 교환학생 경험       심리학과  학부       2015   
3  19    melbourne에서의 한 학기를 마치고..    전기전자공학과  학부     2014-2   
4  18      Melbourne 에서 잊지 못할 1년.       경영학과  학부       2014   
5  17      La Trobe 정말 소중했던 시간들..     물리치료학과  학부  2013-2014   
6  16         La Trobe 그리고 나의 2학년       경영학과  학부       2013   
7  15        I LOVE MELBOURNE!!!♥     불어불문학과  학부       2011   
8  14    아직도 그리운 La Trobe에서의 여유로움       교육학과  학부  2010-2011   
9  13        신촌 대학생, 별이 빛나는 벤디고로!      생활디자인  학부  2010-2011   
0  12              Latrobe에서의 한학기       생물학과  학부       2007   
1  11    축제와 이벤트의 도시 멜번, 그리고 라트로브     신문방송학과  학부       2008   
2  10      소중한 시간 소중한 기억 La Trobe       교육학과  학부  2005-2006   
3   9             La Trobe에서의 1년.    영어영문학전공  학부       2004   
4   8   나에게 소중한 추억을 만들어준 La Trobe    영어영문학전공  학부       

...

   No                    제목    학과  과정    년도  \
0   1  작지만 재미있었던 곳, 웨슬리 대학교  경영학과  학부  2014   

                                           href  
0  /partner/expReport.asp?id=7507&page=1&bgbn=R  
/partner/expReport.asp?id=7507&page=1&bgbn=R
                                            gen_info  \
0  학교는 무척 작습니다. 학생들이 쓰는 건물은 거의 메인 캠퍼스 건물 하나인데. 그 ...   

                                            env_info  \
0  학교 주변에는 사실상 아무 것도 없습니다. 주위가 모두 주택가이고, 조금 걸어나가면...   

                                           food_info  \
0  대부분의 학생들이 기숙사에서 생활합니다. 일부 델라웨어 주서 원래 살고 있는 학생들...   

                                          study_info office_info  \
0  수강신청은 웨슬리 대학 국제처에 있는 직원이 미리 미국에 가기 전에 도움을 줍니다....               

                                          facil_info  \
0  웨슬리 대학은 미국에서 미식축구를 잘하는 대학으로 유명한 학교입니다. 실제로 미식축...   

                                           mhct_info  \
0  저는 사실 딱히 문화 충격을 크게 받은 적은 없었는데, 인상적이었던 것은 학교에 다...   

                                           help_info  \
0 

/partner/expReport.asp?id=3591&page=2&bgbn=R
/partner/expReport.asp?id=3581&page=2&bgbn=R
/partner/expReport.asp?id=3266&page=2&bgbn=R
/partner/expReport.asp?id=3071&page=2&bgbn=R
/partner/expReport.asp?id=2801&page=2&bgbn=R
/partner/expReport.asp?id=2385&page=2&bgbn=R
/partner/expReport.asp?id=2335&page=2&bgbn=R
/partner/expReport.asp?id=2086&page=2&bgbn=R
                                             gen_info  \
0   : 학교 크기는 연세대보다 작다고 느껴졌다. 대체로 평지였지만 공학이나 이과 계열 ...   
1   It is kinda humid in spring,it rains all the t...   
2   WKU의 크기는 연세대학교보다는 조금 더 작은 편입니다. 특히 저 같은 경우에는 기...   
3   보고서를 쓰려고 하니 저도 제 작년 여름에 교환학생 파견보고서를 모두 읽어본 기억이...   
4   다른 분들이 말씀하신 것처럼 캠퍼스는 상당히 연세대와 비슷합니다. 백양로와 같은 긴...   
5   학교 크기 자체는 그렇게 크지 않다. 연세대와 비슷한 정도이나 평지가 많아서 더 다...   
6   학교 크기는 연세대와 비슷합니다. 차이점이 있다면 캠퍼스 내 곳곳에 기숙사가 있다는...   
7   WKU는 Kentucky주의 Bowling Green이란 곳에 있습니다. 크기는 연...   
8   이 부분에 대해서는 앞에서 많은 분들이 설명해주셨으니 간단하게 설명드릴게요. 연대 ...   
9   WKU 의 크기는 연세대학교 크기와 비슷하고, 연세대 보단 낮은 언덕 위에 위치하고...   
10  전체적인 크기는 

   No                                   제목       학과  과정         년도  \
0  19                              행복했던 1년      수학과  학부  2009-2010   
1  18                    Western 에서의 가을 쿼터   UIC 경제  학부       2010   
2  17                   아름다운 학교 WESTERN !!  스포츠레저학과  학부       2009   
3  16                            WWU 경험보고서     의공학부  학부  2008-2009   
4  15  Western Washington University에서의 1년   영어영문학과  학부  2008-2009   
5  14                                    .      심리학  학부       2008   
6  13                               경험보고서-     경영학과  학부  2007-2008   
7  12                           WWU 에서의 일년     생물학과  학부  2007-2008   
8  11       Western Washington Univ. - 이주영   컴퓨터과학과  학부       2006   
9  10                             아름다운 WWU     경영학과  학부       2006   
0   9                    꿈만 같았던 WWU에서의 1년.   신문방송학과  학부  2005-2006   
1   8             Western Washington Univ.     경영학과  학부  2004-2005   
2   7                       WWU 교환학생 경험보고서    경영학전공  학부  2003-2004   
3   6               

   No                                    제목            학과  과정         년도  \
0  23                행복했던 Westminster의 한 학기        정치외교학과  학부       2016   
1  22      후회 없었던 Westminster College에서의 일년          영어영문  학부  2016-2017   
2  21                         웨스트민스터에서의 일 년          심리학과  학부       2016   
3  20            Westminster 에서의 잊지 못할 한 학기          경제학과  학부       2015   
4  19           Westminster College에서의 한 학기        노어노문학과  학부       2016   
5  18               Westminster에서의 여유로웠던 1년     아동가족학/심리학  학부  2015-2016   
6  17                   새로운 문화를 경험할 수 있던 시기  생활디자인/언론홍보영상  학부       2015   
7  16                                최고의 일년          영어영문  학부       2014   
8  15                            많이 성숙했던 시간      디자인/심리학과  학부       2014   
9  14               예상과는 달랐지만 값진 경험이었던 한 학기          경영학과  학부       2015   
0  13           Westminter College 에서의 한학기!           신학과  학부       2013   
1  12        Westminster college에서의 따뜻한 한학기        정치외교학과  학부       2013   
2  11       

   No                       제목    학과  과정    년도  \
0   1  Whitworth College - 김혜원  인문학부  학부  2001   

                                          href  
0  /partner/expReport.asp?id=487&page=1&bgbn=R  
/partner/expReport.asp?id=487&page=1&bgbn=R
                                            gen_info  \
0  내가 다녀온 교환대학은 Washington State 에 위치한 Whitworth ...   

                                            env_info  \
0  Whitworth College는 Seattle에서 비행기로 40분 정도 떨어져 있...   

                                           food_info  \
0  나는 Whitworth College에서 기숙사에 살았다. ISEP으로 가게 되면 ...   

                                          study_info  \
0  내가 미국에 가기 전에 가장 두려워했던 것은 바로 수업이었다. 어학연수와는 달리 교...   

                                         office_info  \
0  이 학교에서 내가 마음 편하게 지낼 수 있었던 것은 국제교육부 스텝들이 너무 따뜻하...   

                                          facil_info mhct_info help_info  \
0  기타 학교의 부대 시설로는 fitness center, music hall, soc...                       

                                       